In [1]:
import asyncio
import logging
import sys
from concurrent.futures import ThreadPoolExecutor
from functools import partial
import time
import os
from datetime import datetime, timedelta
import json

import numpy as np
import pandas as pd
import re
import matplotlib.pyplot as plt

current_path = os.getcwd()

sys.path.append(os.path.join(current_path, "../.."))
from helpers.prompts import (ZERO_SHOT_PROMPT,
                             ZERO_SHOT_ACLED_PROMPT,
                             ZERO_SHOT_JOINT_QUESTION_PROMPT,
                             SCRATCH_PAD_PROMPT,
                             SCRATCH_PAD_ACLED_PROMPT,
                             SCRATCH_PAD_JOINT_QUESTION_PROMPT,
                             REFORMAT_SINGLE_PROMPT,
                             REFORMAT_PROMPT,
                            HUMAN_JOINT_PROMPT_1,
                            HUMAN_JOINT_PROMPT_2,
                            HUMAN_JOINT_PROMPT_3,
                            HUMAN_JOINT_PROMPT_4)
from helpers import model_eval


logger = logging.getLogger()
logger.setLevel(logging.INFO)

/Users/apple/anaconda3/lib/python3.11/site-packages/pandas/core/arrays/masked.py:60: UserWarning: Pandas requires version '1.3.6' or newer of 'bottleneck' (version '1.3.5' currently installed).
  from pandas.core import (


In [2]:
human_joint_prompts = [HUMAN_JOINT_PROMPT_1, 
                    HUMAN_JOINT_PROMPT_2, 
                    HUMAN_JOINT_PROMPT_3, 
                    HUMAN_JOINT_PROMPT_4]

models = {
    "gpt_3p5_turbo_0125": {"source": "OAI", "full_name": "gpt-3.5-turbo-0125"},
    "gpt_4": {"source": "OAI", "full_name": "gpt-4"},
    "gpt_4_turbo_0409": {"source": "OAI", "full_name": "gpt-4-turbo-2024-04-09"},
    "llama_2_70b": {
        "source": "TOGETHER",
        "full_name": "meta-llama/Llama-2-70b-chat-hf",
    },
    "llama_3_8b": {
        "source": "TOGETHER",
        "full_name": "meta-llama/Llama-3-8b-chat-hf",
    },
    "llama_3_70b": {
        "source": "TOGETHER",
        "full_name": "meta-llama/Llama-3-70b-chat-hf",
    },
    "mistral_8x7b_instruct": {
        "source": "TOGETHER",
        "full_name": "mistralai/Mixtral-8x7B-Instruct-v0.1",
    },
    "claude_3_opus": {"source": "ANTHROPIC", "full_name": "claude-3-opus-20240229"},
    "claude_3_sonnet": {"source": "ANTHROPIC", "full_name": "claude-3-sonnet-20240229"},
}

### Load data

In [3]:
import json

def read_jsonl(file_path):
    data = []
    with open(file_path, 'r', encoding='utf-8') as file:
        for line in file:
            if line.strip():  
                json_object = json.loads(line)
                data.append(json_object)
    return data

file_path = '2024-05-03-llm.jsonl'
questions = read_jsonl(file_path)

single_non_acled_questions = [q for q in questions if q['combination_of'] == 'N/A' and q['source'] != 'acled']
single_acled_questions = [q for q in questions if q['combination_of'] == 'N/A' and q['source'] == 'acled']
combo_questions = [q for q in questions if  q['combination_of'] != 'N/A' and q['source'] == 'acled']

In [4]:
len(single_non_acled_questions), len(single_acled_questions), len(combo_questions)

(339, 162, 161)

In [5]:
combo_questions_unrolled = []

for q in combo_questions:
    for i in range(4):
        new_q = q.copy()
        new_q['combo_index'] = i
        
        combo_questions_unrolled.append(new_q)

### Zero Shot Eval

In [6]:
def worker(index, model_name, save_dict, questions_to_eval):
    if save_dict[index] != "":
        return

    logger.info(f"{model_name} - {index}")

    if questions_to_eval[index]['source'] != 'acled':
        prompt = ZERO_SHOT_PROMPT.format(
                    question= questions_to_eval[index]['question'],
                   background= questions_to_eval[index]['background'] + "\n" + questions_to_eval[index]['source_resolution_criteria'],
                   resolution_criteria= questions_to_eval[index]['resolution_criteria'],
                   close_date= questions_to_eval[index]['source_close_datetime'],)
        response = model_eval.get_response_from_model(
            prompt=prompt,
            max_tokens=100,
            model_name=models[model_name]['full_name'],
            temperature=0,
            wait_time=30,
        )

        save_dict[index] = model_eval.extract_probability(response)


    else:
        all_resolution_dates = []
        for horizon in questions_to_eval[index]['forecast_horizons']:
            resolution_date = datetime.fromisoformat(questions_to_eval[index]['freeze_datetime']) + timedelta(days=7 + horizon)
            resolution_date = resolution_date.isoformat()
            all_resolution_dates.append(resolution_date)

        if questions_to_eval[index]['combination_of'] == 'N/A':
            prompt = ZERO_SHOT_ACLED_PROMPT.format(question= questions_to_eval[index]['question'],
                                   background= questions_to_eval[index]['background'] + "\n" + questions_to_eval[index]['source_resolution_criteria'],
                                   resolution_criteria= questions_to_eval[index]['resolution_criteria'],
                                   freeze_datetime= questions_to_eval[index]['freeze_datetime'],
                                   value_at_freeze_datetime= questions_to_eval[index]['value_at_freeze_datetime'],
                                   value_at_freeze_datetime_explanation= questions_to_eval[index]['value_at_freeze_datetime_explanation'],
                                   list_of_resolution_dates= all_resolution_dates)
            response = model_eval.get_response_from_model(
                prompt=prompt,
                max_tokens=100,
                model_name=models[model_name]['full_name'],
                temperature=0,
                wait_time=30,
            )
            
            save_dict[index] = model_eval.reformat_answers(prompt, models, response, questions_to_eval[index])
            
        else:
            prompt = ZERO_SHOT_JOINT_QUESTION_PROMPT.format(human_prompt= human_joint_prompts[questions_to_eval[index]['combo_index']],
                                    question_1= questions_to_eval[index]['combination_of'][0]['question'],                        
                                    question_2= questions_to_eval[index]['combination_of'][1]['question'],
                                   background_1= questions_to_eval[index]['combination_of'][0]['background'] + "\n" + questions_to_eval[index]['combination_of'][0]['source_resolution_criteria'],
                                   background_2= questions_to_eval[index]['combination_of'][1]['background'] + "\n" + questions_to_eval[index]['combination_of'][1]['source_resolution_criteria'],
                                    resolution_criteria_1= questions_to_eval[index]['combination_of'][0]['resolution_criteria'],
                                    resolution_criteria_2= questions_to_eval[index]['combination_of'][1]['resolution_criteria'],
                                   freeze_datetime_1= questions_to_eval[index]['combination_of'][0]['freeze_datetime'],
                                   freeze_datetime_2= questions_to_eval[index]['combination_of'][1]['freeze_datetime'],
                                   value_at_freeze_datetime_1= questions_to_eval[index]['combination_of'][0]['value_at_freeze_datetime'],
                                   value_at_freeze_datetime_2= questions_to_eval[index]['combination_of'][1]['value_at_freeze_datetime'],
                                   value_at_freeze_datetime_explanation_1= questions_to_eval[index]['combination_of'][0]['value_at_freeze_datetime_explanation'],
                                   value_at_freeze_datetime_explanation_2= questions_to_eval[index]['combination_of'][1]['value_at_freeze_datetime_explanation'],
                                   list_of_resolution_dates= all_resolution_dates)
                        
            response = model_eval.get_response_from_model(
                prompt=prompt,
                max_tokens=500,
                model_name=models[model_name]['full_name'],
                temperature=0,
                wait_time=30,
            )
            
            save_dict[index] = model_eval.reformat_answers(prompt, models, response, questions_to_eval[index])
            
    logger.info(save_dict[index])

    return None


def executor(max_workers, model_name, save_dict, questions_to_eval):
    with ThreadPoolExecutor(max_workers=max_workers) as executor:
        worker_with_args = partial(
            worker,
            model_name=model_name,
            save_dict=save_dict,
            questions_to_eval = questions_to_eval
        )
        return list(executor.map(worker_with_args, range(len(questions_to_eval))))

In [7]:
results = {}
model_result_loaded = {}
models_to_test = list(models.keys())[:]

for question in [single_non_acled_questions, single_acled_questions, combo_questions_unrolled]:
    questions_to_eval = question
    if question[0]['source'] != 'acled':
        test_type = 'zero_shot/non_acled'
    elif question[0]['source'] == 'acled' and question[0]['combination_of'] == 'N/A':
        test_type = 'zero_shot/acled'
    else:
        test_type = 'zero_shot/combo'

    for model in models_to_test:
        if model not in model_result_loaded.keys():
            model_result_loaded[model] = {}
        model_result_loaded[model] = False


    for model in models_to_test:
        file_path = f'{test_type}/{model}.jsonl'
        if model not in results.keys():
            results[model] = {}
        try:
            results[model] = read_jsonl(file_path)
            model_result_loaded[model] = True  # Set flag to True if loaded successfully
        except:
            results[model] = {i: "" for i in range(len(questions_to_eval))}


    for model in models_to_test:
        file_path = f'{test_type}/{model}.jsonl'
        if not model_result_loaded[model]:
            executor_count = 15
            if models[model]['source'] != 'ANTHROPIC':
                executor_count = 50
                
            executor(
                executor_count,
                model,
                results[model],
                questions_to_eval
            )

            current_model_forecasts = []
            for index in range(len(questions_to_eval)):
                if questions_to_eval[index]['source'] == 'acled':
                    for forecast, horizon in zip(results[model][index], questions_to_eval[index]['forecast_horizons']):
                        current_forecast = {'id': questions_to_eval[index]['id'],
                           'source': questions_to_eval[index]['source'],
                           'forecast': forecast,
                           'horizon': horizon,
                           'reasoning': None}  
                        if questions_to_eval[index]['combination_of'] != 'N/A':
                            combo_index = questions_to_eval[index]['combo_index']
                            if combo_index == 0:
                                current_forecast['direction'] = [1, 1]
                            elif combo_index == 1:
                                current_forecast['direction'] = [1, 0]
                            elif combo_index == 2:
                                current_forecast['direction'] = [0, 1]
                            else:
                                current_forecast['direction'] = [0, 0]

                        current_model_forecasts.append(current_forecast)
                else:
                    current_forecast = {'id': questions_to_eval[index]['id'],
                                       'source': questions_to_eval[index]['source'],
                                       'forecast': results[model][index],
                                       'reasoning': None}  
                    current_model_forecasts.append(current_forecast)

            os.makedirs(os.path.dirname(file_path), exist_ok=True)
            with open(file_path, 'w') as file:
                for entry in current_model_forecasts:
                    json_line = json.dumps(entry)
                    file.write(json_line + '\n')


In [17]:
prompt_type = 'zero_shot'

for model in models_to_test:
    current_model_forecasts = []
    for test_type in [f'{prompt_type}/non_acled', f'{prompt_type}/acled',f'{prompt_type}/combo']:
        file_path = f'{test_type}/{model}.jsonl'
        questions = read_jsonl(file_path)
        current_model_forecasts.append(questions)
        
    final_file_name = f'{prompt_type}/final/{model}'
    os.makedirs(os.path.dirname(final_file_name), exist_ok=True)
    with open(final_file_name, 'w') as file:
        for entry in current_model_forecasts:
            json_line = json.dumps(entry)
            file.write(json_line + '\n')

### Scratchpad

In [14]:
def worker(index, model_name, save_dict, questions_to_eval):
    if save_dict[index] != "":
        return
    
    logger.info(f"Starting {model_name} - {index}")

    if questions_to_eval[index]['source'] != 'acled':
        prompt = SCRATCH_PAD_PROMPT.format(
                    question= questions_to_eval[index]['question'],
                   background= questions_to_eval[index]['background'] + "\n" + questions_to_eval[index]['source_resolution_criteria'],
                   resolution_criteria= questions_to_eval[index]['resolution_criteria'],
                   close_date= questions_to_eval[index]['source_close_datetime'],)
        response = model_eval.get_response_from_model(
            prompt=prompt,
            max_tokens=1300,
            model_name=models[model_name]['full_name'],
            temperature=0,
            wait_time=30,
        )

        save_dict[index] = (model_eval.reformat_answers(response = response, models= models, single = True), response)

    else:
        all_resolution_dates = []
        for horizon in questions_to_eval[index]['forecast_horizons']:
            resolution_date = datetime.fromisoformat(questions_to_eval[index]['freeze_datetime']) + timedelta(days=7 + horizon)
            resolution_date = resolution_date.isoformat()
            all_resolution_dates.append(resolution_date)

        if questions_to_eval[index]['combination_of'] == 'N/A':
            prompt = SCRATCH_PAD_ACLED_PROMPT.format(question= questions_to_eval[index]['question'],
                                   background= questions_to_eval[index]['background'] + "\n" + questions_to_eval[index]['source_resolution_criteria'],
                                   resolution_criteria= questions_to_eval[index]['resolution_criteria'],
                                   freeze_datetime= questions_to_eval[index]['freeze_datetime'],
                                   value_at_freeze_datetime= questions_to_eval[index]['value_at_freeze_datetime'],
                                   value_at_freeze_datetime_explanation= questions_to_eval[index]['value_at_freeze_datetime_explanation'],
                                   list_of_resolution_dates= all_resolution_dates)
            response = model_eval.get_response_from_model(
                prompt=prompt,
                max_tokens=2000,
                model_name=models[model_name]['full_name'],
                temperature=0,
                wait_time=30,
            )
            save_dict[index] = (model_eval.reformat_answers(response = response, 
                                                            models = models, 
                                                            prompt = prompt,
                                                            question = questions_to_eval[index]), 
                                response)
        else:
            prompt = SCRATCH_PAD_JOINT_QUESTION_PROMPT.format(human_prompt= human_joint_prompts[questions_to_eval[index]['combo_index']],
                                    question_1= questions_to_eval[index]['combination_of'][0]['question'],                        
                                    question_2= questions_to_eval[index]['combination_of'][1]['question'],
                                   background_1= questions_to_eval[index]['combination_of'][0]['background'] + "\n" + questions_to_eval[index]['combination_of'][0]['source_resolution_criteria'],
                                   background_2= questions_to_eval[index]['combination_of'][1]['background'] + "\n" + questions_to_eval[index]['combination_of'][1]['source_resolution_criteria'],
                                    resolution_criteria_1= questions_to_eval[index]['combination_of'][0]['resolution_criteria'],
                                    resolution_criteria_2= questions_to_eval[index]['combination_of'][1]['resolution_criteria'],
                                   freeze_datetime_1= questions_to_eval[index]['combination_of'][0]['freeze_datetime'],
                                   freeze_datetime_2= questions_to_eval[index]['combination_of'][1]['freeze_datetime'],
                                   value_at_freeze_datetime_1= questions_to_eval[index]['combination_of'][0]['value_at_freeze_datetime'],
                                   value_at_freeze_datetime_2= questions_to_eval[index]['combination_of'][1]['value_at_freeze_datetime'],
                                   value_at_freeze_datetime_explanation_1= questions_to_eval[index]['combination_of'][0]['value_at_freeze_datetime_explanation'],
                                   value_at_freeze_datetime_explanation_2= questions_to_eval[index]['combination_of'][1]['value_at_freeze_datetime_explanation'],
                                   list_of_resolution_dates= all_resolution_dates)
                        
            response = model_eval.get_response_from_model(
                prompt=prompt,
                max_tokens=2000,
                model_name=models[model_name]['full_name'],
                temperature=0,
                wait_time=30,
            )
            
            save_dict[index] = (model_eval.reformat_answers(response = response, models = models, prompt = prompt, question = questions_to_eval[index]),
                                response)
            
    logger.info(f"Answer {save_dict[index][0]}")

    return None


def executor(max_workers, model_name, save_dict, questions_to_eval):
    with ThreadPoolExecutor(max_workers=max_workers) as executor:
        worker_with_args = partial(
            worker,
            model_name=model_name,
            save_dict=save_dict,
            questions_to_eval=questions_to_eval
        )
        return list(executor.map(worker_with_args, range(len(questions_to_eval))))

In [15]:
results = {}
model_result_loaded = {}
models_to_test = list(models.keys())[:]


for question in [single_acled_questions, single_non_acled_questions, combo_questions_unrolled]:
    questions_to_eval = question
    if question[0]['source'] != 'acled':
        test_type = 'scratchpad/non_acled'
    elif question[0]['source'] == 'acled' and question[0]['combination_of'] == 'N/A':
        test_type = 'scratchpad/acled'
    else:
        test_type = 'scratchpad/combo'


    for model in models_to_test:
        if model not in model_result_loaded.keys():
            model_result_loaded[model] = {}
        model_result_loaded[model] = False

    for model in models_to_test:
        file_path = f'{test_type}/{model}.jsonl'
        if model not in results.keys():
            results[model] = {}
        try:
            results[model] = read_jsonl(file_path)
            model_result_loaded[model] = True  # Set flag to True if loaded successfully
        except:
            results[model] = {i: "" for i in range(len(questions_to_eval))}


    for model in models_to_test:
        file_path = f'{test_type}/{model}.jsonl'
        if not model_result_loaded[model]:
            executor_count = 10
            if models[model]['source'] != 'ANTHROPIC':
                executor_count = 50
                
            executor(
                executor_count,
                model,
                results[model],
                questions_to_eval
            )

            current_model_forecasts = []
            for index in range(len(questions_to_eval)):
                if questions_to_eval[index]['source'] == 'acled':
                    for forecast, horizon in zip(results[model][index][0], questions_to_eval[index]['forecast_horizons']):
                        current_forecast = {'id': questions_to_eval[index]['id'],
                           'source': questions_to_eval[index]['source'],
                           'forecast': forecast,
                           'horizon': horizon,
                           'reasoning': results[model][index][1]}  
                        
                        if questions_to_eval[index]['combination_of'] != 'N/A':
                            combo_index = questions_to_eval[index]['combo_index']
                            if combo_index == 0:
                                current_forecast['direction'] = [1, 1]
                            elif combo_index == 1:
                                current_forecast['direction'] = [1, 0]
                            elif combo_index == 2:
                                current_forecast['direction'] = [0, 1]
                            else:
                                current_forecast['direction'] = [0, 0]

                        current_model_forecasts.append(current_forecast)
                        
                else:
                    current_forecast = {'id': questions_to_eval[index]['id'],
                                       'source': questions_to_eval[index]['source'],
                                       'forecast': results[model][index][0],
                                       'reasoning': results[model][index][1]}  
                    current_model_forecasts.append(current_forecast)


            os.makedirs(os.path.dirname(file_path), exist_ok=True)
            with open(file_path, 'w') as file:
                for entry in current_model_forecasts:
                    json_line = json.dumps(entry)
                    file.write(json_line + '\n')


INFO:root:Starting gpt_3p5_turbo_0125 - 0
INFO:root:Starting gpt_3p5_turbo_0125 - 1
INFO:root:Starting gpt_3p5_turbo_0125 - 2
INFO:root:Starting gpt_3p5_turbo_0125 - 3
INFO:root:Starting gpt_3p5_turbo_0125 - 4
INFO:root:Starting gpt_3p5_turbo_0125 - 5
INFO:root:Starting gpt_3p5_turbo_0125 - 6
INFO:root:Starting gpt_3p5_turbo_0125 - 7
INFO:root:Starting gpt_3p5_turbo_0125 - 8
INFO:root:Starting gpt_3p5_turbo_0125 - 9
INFO:root:Starting gpt_3p5_turbo_0125 - 10
INFO:root:Starting gpt_3p5_turbo_0125 - 11
INFO:root:Starting gpt_3p5_turbo_0125 - 12
INFO:root:Starting gpt_3p5_turbo_0125 - 13
INFO:root:Starting gpt_3p5_turbo_0125 - 14
INFO:root:Starting gpt_3p5_turbo_0125 - 15
INFO:root:Starting gpt_3p5_turbo_0125 - 16
INFO:root:Starting gpt_3p5_turbo_0125 - 17
INFO:root:Starting gpt_3p5_turbo_0125 - 18
INFO:root:Starting gpt_3p5_turbo_0125 - 19
INFO:root:Starting gpt_3p5_turbo_0125 - 20
INFO:root:Starting gpt_3p5_turbo_0125 - 21
INFO:root:Starting gpt_3p5_turbo_0125 - 22
INFO:root:Starting gp

INFO:httpx:HTTP Request: POST https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"
INFO:root:Answer [0.5, 0.5, 0.5, 0.5, 0.5, 0.5, 0.5, 0.5]
INFO:root:Starting gpt_3p5_turbo_0125 - 66
INFO:httpx:HTTP Request: POST https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"
INFO:httpx:HTTP Request: POST https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"
INFO:root:Answer [0.6, 0.6, 0.6, 0.6, 0.6, 0.6, 0.6, 0.6]
INFO:root:Starting gpt_3p5_turbo_0125 - 67
INFO:httpx:HTTP Request: POST https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"
INFO:root:Answer [0.6, 0.6, 0.6, 0.6, 0.6, 0.6, 0.6, 0.6]
INFO:root:Starting gpt_3p5_turbo_0125 - 68
INFO:httpx:HTTP Request: POST https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"
INFO:root:Answer [0.6, 0.6, 0.6, 0.6, 0.6, 0.6, 0.6, 0.6]
INFO:root:Starting gpt_3p5_turbo_0125 - 69
INFO:httpx:HTTP Request: POST https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"
INFO:httpx:HTTP Request: POST https://api.openai.c

INFO:httpx:HTTP Request: POST https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"
INFO:httpx:HTTP Request: POST https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"
INFO:httpx:HTTP Request: POST https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"
INFO:root:Answer [0.35, 0.35, 0.35, 0.35, 0.35, 0.35, 0.35, 0.35]
INFO:root:Starting gpt_3p5_turbo_0125 - 99
INFO:httpx:HTTP Request: POST https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"
INFO:httpx:HTTP Request: POST https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"
INFO:root:Answer [0.45, 0.45, 0.45, 0.45, 0.45, 0.45, 0.45, 0.45]
INFO:root:Starting gpt_3p5_turbo_0125 - 100
INFO:httpx:HTTP Request: POST https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"
INFO:httpx:HTTP Request: POST https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"
INFO:root:Answer [0.5, 0.5, 0.5, 0.5, 0.5, 0.5, 0.5, 0.5]
INFO:root:Starting gpt_3p5_turbo_0125 - 101
INFO:httpx:HTTP Request: POST https://api.

INFO:root:Starting gpt_3p5_turbo_0125 - 126
INFO:httpx:HTTP Request: POST https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"
INFO:root:Answer [0.5, 0.5, 0.5, 0.5, 0.5, 0.5, 0.5, 0.5]
INFO:root:Starting gpt_3p5_turbo_0125 - 127
INFO:httpx:HTTP Request: POST https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"
INFO:root:Answer [0.45, 0.45, 0.45, 0.45, 0.45, 0.45, 0.45, 0.45]
INFO:root:Starting gpt_3p5_turbo_0125 - 128
INFO:httpx:HTTP Request: POST https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"
INFO:root:Answer [0.6, 0.6, 0.6, 0.6, 0.6, 0.6, 0.6, 0.6]
INFO:root:Starting gpt_3p5_turbo_0125 - 129
INFO:httpx:HTTP Request: POST https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"
INFO:root:Answer [0.6, 0.6, 0.6, 0.6, 0.6, 0.6, 0.6, 0.6]
INFO:root:Starting gpt_3p5_turbo_0125 - 130
INFO:httpx:HTTP Request: POST https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"
INFO:httpx:HTTP Request: POST https://api.openai.com/v1/chat/completions "HTTP/1.1 20

INFO:root:Answer [0.5, 0.5, 0.5, 0.5, 0.5, 0.5, 0.5, 0.5]
INFO:root:Starting gpt_3p5_turbo_0125 - 154
INFO:httpx:HTTP Request: POST https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"
INFO:httpx:HTTP Request: POST https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"
INFO:httpx:HTTP Request: POST https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"
INFO:root:Answer [0.5, 0.5, 0.5, 0.5, 0.5, 0.5, 0.5, 0.5]
INFO:root:Starting gpt_3p5_turbo_0125 - 155
INFO:httpx:HTTP Request: POST https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"
INFO:root:Answer [0.45, 0.45, 0.45, 0.45, 0.45, 0.45, 0.45, 0.45]
INFO:root:Starting gpt_3p5_turbo_0125 - 156
INFO:httpx:HTTP Request: POST https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"
INFO:httpx:HTTP Request: POST https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"
INFO:httpx:HTTP Request: POST https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"
INFO:root:Answer [0.45, 0.45, 0.45, 0.45, 0.45, 0

...

INFO:helpers.model_eval:Waiting for 30 seconds before retrying...
INFO:httpx:HTTP Request: POST https://api.anthropic.com/v1/messages "HTTP/1.1 429 Too Many Requests"
INFO:helpers.model_eval:Anthropic API request exceeded rate limit.: Error code: 429 - {'type': 'error', 'error': {'type': 'rate_limit_error', 'message': 'Number of concurrent connections has exceeded your rate limit. Please try again later or contact sales at https://www.anthropic.com/contact-sales to discuss your options for a rate limit increase.'}}
INFO:helpers.model_eval:Waiting for 30 seconds before retrying...
INFO:httpx:HTTP Request: POST https://api.anthropic.com/v1/messages "HTTP/1.1 200 OK"
INFO:httpx:HTTP Request: POST https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"
INFO:root:Answer [0.75, 0.73, 0.71, 0.69, 0.67, 0.65, 0.63, 0.61]
INFO:root:Starting claude_3_sonnet - 631
INFO:httpx:HTTP Request: POST https://api.anthropic.com/v1/messages "HTTP/1.1 200 OK"
INFO:httpx:HTTP Request: POST https://api.o

INFO:helpers.model_eval:Waiting for 30 seconds before retrying...
INFO:httpx:HTTP Request: POST https://api.anthropic.com/v1/messages "HTTP/1.1 429 Too Many Requests"
INFO:helpers.model_eval:Anthropic API request exceeded rate limit.: Error code: 429 - {'type': 'error', 'error': {'type': 'rate_limit_error', 'message': 'Number of concurrent connections has exceeded your rate limit. Please try again later or contact sales at https://www.anthropic.com/contact-sales to discuss your options for a rate limit increase.'}}
INFO:helpers.model_eval:Waiting for 30 seconds before retrying...
INFO:httpx:HTTP Request: POST https://api.anthropic.com/v1/messages "HTTP/1.1 200 OK"
INFO:httpx:HTTP Request: POST https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"
INFO:root:Answer [0.85, 0.82, 0.8, 0.78, 0.75, 0.73, 0.7, 0.68]
INFO:root:Starting claude_3_sonnet - 635
INFO:httpx:HTTP Request: POST https://api.anthropic.com/v1/messages "HTTP/1.1 200 OK"
INFO:httpx:HTTP Request: POST https://api.ope

INFO:helpers.model_eval:Anthropic API request exceeded rate limit.: Error code: 429 - {'type': 'error', 'error': {'type': 'rate_limit_error', 'message': 'Number of concurrent connections has exceeded your rate limit. Please try again later or contact sales at https://www.anthropic.com/contact-sales to discuss your options for a rate limit increase.'}}
INFO:helpers.model_eval:Waiting for 30 seconds before retrying...
INFO:httpx:HTTP Request: POST https://api.anthropic.com/v1/messages "HTTP/1.1 429 Too Many Requests"
INFO:helpers.model_eval:Anthropic API request exceeded rate limit.: Error code: 429 - {'type': 'error', 'error': {'type': 'rate_limit_error', 'message': 'Number of concurrent connections has exceeded your rate limit. Please try again later or contact sales at https://www.anthropic.com/contact-sales to discuss your options for a rate limit increase.'}}
INFO:helpers.model_eval:Waiting for 30 seconds before retrying...
INFO:httpx:HTTP Request: POST https://api.anthropic.com/v1/

INFO:helpers.model_eval:Anthropic API request exceeded rate limit.: Error code: 429 - {'type': 'error', 'error': {'type': 'rate_limit_error', 'message': 'Number of concurrent connections has exceeded your rate limit. Please try again later or contact sales at https://www.anthropic.com/contact-sales to discuss your options for a rate limit increase.'}}
INFO:helpers.model_eval:Waiting for 30 seconds before retrying...
INFO:httpx:HTTP Request: POST https://api.anthropic.com/v1/messages "HTTP/1.1 429 Too Many Requests"
INFO:helpers.model_eval:Anthropic API request exceeded rate limit.: Error code: 429 - {'type': 'error', 'error': {'type': 'rate_limit_error', 'message': 'Number of concurrent connections has exceeded your rate limit. Please try again later or contact sales at https://www.anthropic.com/contact-sales to discuss your options for a rate limit increase.'}}
INFO:helpers.model_eval:Waiting for 30 seconds before retrying...
INFO:httpx:HTTP Request: POST https://api.anthropic.com/v1/

INFO:anthropic._base_client:Retrying request to /v1/messages in 0.977436 seconds
INFO:httpx:HTTP Request: POST https://api.anthropic.com/v1/messages "HTTP/1.1 429 Too Many Requests"
INFO:anthropic._base_client:Retrying request to /v1/messages in 0.800760 seconds
INFO:httpx:HTTP Request: POST https://api.anthropic.com/v1/messages "HTTP/1.1 429 Too Many Requests"
INFO:anthropic._base_client:Retrying request to /v1/messages in 1.764692 seconds
INFO:httpx:HTTP Request: POST https://api.anthropic.com/v1/messages "HTTP/1.1 429 Too Many Requests"
INFO:anthropic._base_client:Retrying request to /v1/messages in 1.630953 seconds
INFO:httpx:HTTP Request: POST https://api.anthropic.com/v1/messages "HTTP/1.1 429 Too Many Requests"
INFO:helpers.model_eval:Anthropic API request exceeded rate limit.: Error code: 429 - {'type': 'error', 'error': {'type': 'rate_limit_error', 'message': 'Number of concurrent connections has exceeded your rate limit. Please try again later or contact sales at https://www.

In [16]:
prompt_type = 'scratchpad'

for model in models_to_test:
    current_model_forecasts = []
    for test_type in [f'{prompt_type}/non_acled', f'{prompt_type}/acled',f'{prompt_type}/combo']:
        file_path = f'{test_type}/{model}.jsonl'
        questions = read_jsonl(file_path)
        current_model_forecasts.append(questions)
        
    final_file_name = f'{prompt_type}/final/{model}'
    os.makedirs(os.path.dirname(final_file_name), exist_ok=True)
    with open(final_file_name, 'w') as file:
        for entry in current_model_forecasts:
            json_line = json.dumps(entry)
            file.write(json_line + '\n')